In [691]:
import pandas as pd
import numpy as np
import geopandas as gp
import folium
import re

## Neighborhood Geo Data

In [692]:
gNeigh=gp.read_file("Data/Zones/NTA map.geojson")

In [693]:
gNeigh=gNeigh[['ntacode','ntaname','boroname','geometry']].sort_values('ntacode').reset_index(drop=True)
gNeigh['lat']=gNeigh.centroid.y
gNeigh['long']=gNeigh.centroid.x
gNeigh.rename({'ntacode':'code','ntaname':'name','boroname':'borough'},axis=1,inplace=True)
print(gNeigh.shape)
gNeigh.tail()

(195, 6)


code                             name        borough  \
190  SI37               Stapleton-Rosebank  Staten Island   
191  SI45           New Dorp-Midland Beach  Staten Island   
192  SI48                    Arden Heights  Staten Island   
193  SI54                      Great Kills  Staten Island   
194  SI99  park-cemetery-etc-Staten Island  Staten Island   

                                              geometry        lat       long  
190  (POLYGON ((-74.07258133873532 40.6379418745920...  40.618775 -74.073707  
191  (POLYGON ((-74.08469075991437 40.5714779139397...  40.571769 -74.105010  
192  (POLYGON ((-74.17185166456863 40.5615209230212...  40.552658 -74.188483  
193  (POLYGON ((-74.144387450266 40.56970610066725,...  40.551863 -74.150889  
194  (POLYGON ((-74.11813477632811 40.5505926931505...  40.546588 -74.126354

## Population Data

In [694]:
pop=pd.read_excel("Data/Demographic/NYPopNTA.xlsx",usecols=range(0,121))
cols=list(range(1,5))+[119]
pop=pop.iloc[:,cols].sort_values('GeoID').reset_index(drop=True)
pop.rename({'Pop_1E':'population','MdAgeE':'medAge','GeoID':'code','GeoName':'name','Borough':'borough'},axis=1,inplace=True)

In [695]:
print(pop.shape)
pop.head()

(195, 5)


name  code   borough  population  \
0                    Brooklyn Heights-Cobble Hill  BK09  Brooklyn       24212   
1  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  BK17  Brooklyn       67681   
2                                  Brighton Beach  BK19  Brooklyn       35811   
3                            Seagate-Coney Island  BK21  Brooklyn       31132   
4                                   West Brighton  BK23  Brooklyn       16436   

   medAge  
0    37.1  
1    43.9  
2    44.3  
3    39.0  
4    58.0

In [696]:
dayPop=pd.read_excel("Data/Demographic/daytimePop.xls",usecols="G,H,R",names=['borough','total','dayChange'],skiprows=6).dropna()
dayPop=dayPop.iloc[[1552,1676,1590,1448,1687],[0,2]].reset_index(drop=True)
dayPop['borough']=dayPop['borough'].apply(lambda x:str.split(x)[0])
dayPop['borough'].replace('Staten','Staten Island',inplace=True)
dayPop

borough  dayChange
0       Brooklyn      -12.0
1         Queens      -16.1
2      Manhattan       94.7
3          Bronx      -11.7
4  Staten Island      -17.7

In [697]:
dayPopulation=[]
for i,row in pop.iterrows():
    dayPopulation.append(row['population']+round(row['population']*((dayPop.loc[dayPop['borough']==row['borough'],'dayChange'].values[0])/100),0))
# dayPop.loc[dayPop['borough']==row['borough'],'dayChange']
pop['dayPop']=dayPopulation

In [698]:
pop.head()

name  code   borough  population  \
0                    Brooklyn Heights-Cobble Hill  BK09  Brooklyn       24212   
1  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  BK17  Brooklyn       67681   
2                                  Brighton Beach  BK19  Brooklyn       35811   
3                            Seagate-Coney Island  BK21  Brooklyn       31132   
4                                   West Brighton  BK23  Brooklyn       16436   

   medAge   dayPop  
0    37.1  21307.0  
1    43.9  59559.0  
2    44.3  31514.0  
3    39.0  27396.0  
4    58.0  14464.0

## Economic Data

In [699]:
cols="B:D,IX:LC"
income=pd.read_excel("Data/Demographic/NYEconNTA.xlsx",usecols=cols)
income.drop([x for x in income.columns.values if re.match(".*[MPCZ]$",x)],axis=1,inplace=True)

In [700]:
income['veryLow']=income.iloc[:,3:6].sum(axis=1)
income['low']=income.iloc[:,6:8].sum(axis=1)
income['middle']=income.iloc[:,8:10].sum(axis=1)
income['high']=income.iloc[:,10:12].sum(axis=1)
income['veryHigh']=income.iloc[:,12]
income.drop(income.iloc[:,3:13],axis=1,inplace=True)
income.sort_values('GeoID',inplace=True)
income.rename({'MdHHIncE':'medIncome','MnHHIncE':'meanIncome','GeoID':'code','GeoName':'name','Borough':'borough'},
              axis=1,inplace=True)
income.reset_index(drop=True,inplace=True)

In [701]:
print(income.shape)
income.head()

(195, 10)


name  code   borough  medIncome  \
0                    Brooklyn Heights-Cobble Hill  BK09  Brooklyn   125817.0   
1  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  BK17  Brooklyn    57150.0   
2                                  Brighton Beach  BK19  Brooklyn    36802.0   
3                            Seagate-Coney Island  BK21  Brooklyn    27345.0   
4                                   West Brighton  BK23  Brooklyn    40316.0   

   meanIncome  veryLow   low  middle  high  veryHigh  
0    205275.0     1279  1201    2008  3355      3272  
1     79613.0     6637  5298    6797  5785      1633  
2     63703.0     5762  2697    3301  2006       791  
3     49358.0     5381  2285    2158  1115       297  
4     58752.0     3169  1790    2212   955       275

## Housing Data

In [702]:
cols="B:D,LR,RB"
rent=pd.read_excel("Data/Demographic/NYHousNTA.xlsx",usecols=cols)
rent.sort_values('GeoID',inplace=True)
rent.rename({'MdVlE':'medValue','MdGRE':'medRent','GeoID':'code','GeoName':'name','Borough':'borough'},
              axis=1,inplace=True)
rent.reset_index(drop=True,inplace=True)

In [703]:
print(rent.shape)
rent.head()

(195, 5)


name  code   borough  medValue  \
0                    Brooklyn Heights-Cobble Hill  BK09  Brooklyn  856535.0   
1  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  BK17  Brooklyn  476965.0   
2                                  Brighton Beach  BK19  Brooklyn  561046.0   
3                            Seagate-Coney Island  BK21  Brooklyn  457834.0   
4                                   West Brighton  BK23  Brooklyn  311186.0   

   medRent  
0   2278.0  
1   1180.0  
2   1194.0  
3    676.0  
4    905.0

## Traffic Geo Data

In [704]:
gTraffic=gp.read_file("Data/Traffic/AADT.shp")
gTraffic.crs={'init': 'epsg:4326'}

In [705]:
gTraffic['AADT']=gTraffic['AADT'].replace(0,np.NaN)
gTraffic.dropna(inplace=True)
gTraffic.reset_index(drop=True,inplace=True)
gTraffic.rename({'TDV_ROUTE':'road','Type':'type'},axis=1,inplace=True)
gTraffic.head()

road      AADT   type  \
0  I87 NB to Grand Concourse    9098.0   Ramp   
1                 BARTOW AVE   18317.0   Road   
2              E TREMONT AVE   15891.0   Road   
3              E TREMONT AVE   21551.0   Road   
4      I87, MAJOR DEEGAN EXP  102213.0  Route   

                                            geometry  
0  LINESTRING (-73.93120499291497 40.811187005174...  
1  LINESTRING (-73.83174595168754 40.868683967375...  
2  LINESTRING (-73.87297299845201 40.839735862949...  
3  LINESTRING (-73.86477339345717 40.840984407520...  
4  LINESTRING (-73.91907386627308 40.804683954394...

### Consolidate Traffic GeoData from Roads into Areas

In [706]:
nTraffic=gp.tools.sjoin(gNeigh,gTraffic,op='intersects')
nTraffic.drop('index_right',axis=1,inplace=True)
nTraffic.sort_values('code',inplace=True)
nTraffic=nTraffic[nTraffic['type']!="Route"]
nTraffic.reset_index(drop=True,inplace=True)
nTraffic.head()

code                          name   borough  \
0  BK09  Brooklyn Heights-Cobble Hill  Brooklyn   
1  BK09  Brooklyn Heights-Cobble Hill  Brooklyn   
2  BK09  Brooklyn Heights-Cobble Hill  Brooklyn   
3  BK09  Brooklyn Heights-Cobble Hill  Brooklyn   
4  BK09  Brooklyn Heights-Cobble Hill  Brooklyn   

                                            geometry        lat       long  \
0  (POLYGON ((-73.99236367043254 40.689690123777,...  40.695469 -73.994871   
1  (POLYGON ((-73.99236367043254 40.689690123777,...  40.695469 -73.994871   
2  (POLYGON ((-73.99236367043254 40.689690123777,...  40.695469 -73.994871   
3  (POLYGON ((-73.99236367043254 40.689690123777,...  40.695469 -73.994871   
4  (POLYGON ((-73.99236367043254 40.689690123777,...  40.695469 -73.994871   

             road     AADT  type  
0        COURT ST  11136.0  Road  
1  CADMAN PLAZA W  10408.0  Road  
2       FURMAN ST   6131.0  Road  
3      TILLARY ST  14123.0  Road  
4        HENRY ST   5126.0  Road

In [707]:
traffic=nTraffic.groupby('name').agg({"code":lambda x:np.unique(x),
                                    'AADT':lambda x:np.mean(x),
                                    'borough':lambda x:np.unique(x),
                                    'lat':lambda x:np.unique(x),
                                    'long':lambda x:np.unique(x)
                                    }).sort_values('code')
traffic=gp.GeoDataFrame(aadts,crs={'init': 'epsg:4326'},geometry=list(gNeigh.geometry)).reset_index(drop=True)
traffic.loc[194,'AADT']=np.NaN
print(traffic.shape)
traffic.head()

(195, 7)


name  code          AADT  \
0                    Brooklyn Heights-Cobble Hill  BK09  11051.190476   
1  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  BK17  12013.800000   
2                                  Brighton Beach  BK19  12252.733333   
3                            Seagate-Coney Island  BK21  15428.300000   
4                                   West Brighton  BK23   8256.600000   

    borough        lat       long  \
0  Brooklyn  40.695469 -73.994871   
1  Brooklyn  40.588300 -73.941511   
2  Brooklyn  40.580922 -73.961217   
3  Brooklyn  40.576480 -73.991231   
4  Brooklyn  40.579088 -73.973391   

                                            geometry  
0  (POLYGON ((-73.99236367043254 40.689690123777,...  
1  (POLYGON ((-73.91809256480843 40.5865703350047...  
2  (POLYGON ((-73.96034953585246 40.5873062855713...  
3  (POLYGON ((-73.97459000582634 40.5831388207588...  
4  (POLYGON ((-73.9688899587795 40.57526123899416...

In [708]:
data=gNeigh[['code','name','lat','long','borough']]
data=data.merge(pop).merge(rent).merge(income)

In [709]:
df=gp.GeoDataFrame(data,crs={'init': 'epsg:4326'},geometry=list(gNeigh.geometry))
print(df.shape)
df.head()

(195, 18)


code                                            name        lat       long  \
0  BK09                    Brooklyn Heights-Cobble Hill  40.695469 -73.994871   
1  BK17  Sheepshead Bay-Gerritsen Beach-Manhattan Beach  40.588300 -73.941511   
2  BK19                                  Brighton Beach  40.580922 -73.961217   
3  BK21                            Seagate-Coney Island  40.576480 -73.991231   
4  BK23                                   West Brighton  40.579088 -73.973391   

    borough  population  medAge   dayPop  medValue  medRent  medIncome  \
0  Brooklyn       24212    37.1  21307.0  856535.0   2278.0   125817.0   
1  Brooklyn       67681    43.9  59559.0  476965.0   1180.0    57150.0   
2  Brooklyn       35811    44.3  31514.0  561046.0   1194.0    36802.0   
3  Brooklyn       31132    39.0  27396.0  457834.0    676.0    27345.0   
4  Brooklyn       16436    58.0  14464.0  311186.0    905.0    40316.0   

   meanIncome  veryLow   low  middle  high  veryHigh  \
0    205275.0     1279  1201    2008  3355      3272   
1     79613.0     6637  5298    6797  5785      1633   
2     63703.0     5762  2697    3301  2006       791   
3     49358.0     5381  2285    2158  1115       297   
4     58752.0     3169  1790    2212   955       275   

                                            geometry  
0  (POLYGON ((-73.99236367043254 40.689690123777,...  
1  (POLYGON ((-73.91809256480843 40.5865703350047...  
2  (POLYGON ((-73.96034953585246 40.5873062855713...  
3  (POLYGON ((-73.97459000582634 40.5831388207588...  
4  (POLYGON ((-73.9688899587795 40.57526123899416...

In [715]:
df.to_csv('Data/Cleaned/data.csv')

In [710]:
ny=folium.Map((40.7128,-74.0060),zoom_start=10)
choro=folium.Choropleth(df,
                  columns=['name','medIncome'],
                  data=df,
                  key_on='feature.properties.name',
                  fill_color='YlOrRd',
                    highlight=True
                 )
choro.add_to(ny)
ny

In [ ]:
url="https://nominatim.openstreetmap.org/search?"+"q=Bronx&format=geojson&limit=1&addressdetails=1&polygon_geojson=1"
bronx=requests.get(url).json()